In [2]:
import sys
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [8]:
expr = pd.DataFrame(pd.read_csv("GSE185070_SIvsBM_varianceStabilizedExpression.txt", sep="\t", header=0))
ih_df = pd.read_csv("GSE185070-GPL21103-ih.txt", sep="\t", header=0) 
expr.columns = ["Name", "ProbeID"]+list(ih_df["ArrayID"])
cols = ["ProbeID", "Name"]+list(ih_df["ArrayID"])
expr = expr[cols]
expr

ProbeID        Name  GSM5605685  GSM5605686  GSM5605687  \
0      ENSMUSG00000064339     mt-Rnr2   21.061843   21.183851   20.583707   
1      ENSMUSG00000092341      Malat1   15.026790   15.104005   15.128319   
2      ENSMUSG00000106106  CT010467.1   19.310684   19.032210   19.005368   
3      ENSMUSG00000064337     mt-Rnr1   17.844402   17.841443   17.841444   
4      ENSMUSG00000040152       Thbs1    8.095342    7.246238    7.866982   
...                   ...         ...         ...         ...         ...   
38387  ENSMUSG00000106538     Gm30301    0.929716    1.762246    0.929716   
38388  ENSMUSG00000106619      Gm9353    0.929716    1.762246    0.929716   
38389  ENSMUSG00000106640     Gm20940    0.929716    1.762246    0.929716   
38390  ENSMUSG00000106660     Gm43472    0.929716    1.762246    0.929716   
38391  ENSMUSG00000106955     Gm42960    0.929716    1.762246    0.929716   

       GSM5605688  GSM5605689  GSM5605690  GSM5605691  GSM5605692  
0       20.996477   20.059160   20.469747   21.170331   20.590137  
1       15.053929   18.182545   18.377585   17.956084   18.237156  
2       18.686055   17.726752   18.220837   17.773668   17.746255  
3       17.609733   16.829512   17.476988   18.118180   17.445740  
4        7.465235   17.700392   17.464732   16.828615   17.291607  
...           ...         ...         ...         ...         ...  
38387    0.929716    0.929716    0.929716    0.929716    0.929716  
38388    0.929716    0.929716    0.929716    0.929716    0.929716  
38389    0.929716    0.929716    0.929716    0.929716    0.929716  
38390    0.929716    0.929716    0.929716    0.929716    0.929716  
38391    0.929716    0.929716    0.929716    0.929716    0.929716  

[38392 rows x 10 columns]

In [9]:
genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

path_dir = "./"
expr.to_csv(path_dir+"GSE185070-GPL21103-expr.txt", header=True, index=False,sep='\t')
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID        Name  GSM5605685  GSM5605686  GSM5605687  \
0      ENSMUSG00000064339     mt-Rnr2    7.257740    7.208223    7.230833   
1      ENSMUSG00000092341      Malat1    6.774426    6.724112    6.790041   
2      ENSMUSG00000106106  CT010467.1    7.133361    7.054804    7.116535   
3      ENSMUSG00000064337     mt-Rnr1    7.020278    6.962318    7.026038   
4      ENSMUSG00000040152       Thbs1    5.893293    5.679207    5.858655   
...                   ...         ...         ...         ...         ...   
38387  ENSMUSG00000106538     Gm30301    2.946966    3.724451    2.952228   
38388  ENSMUSG00000106619      Gm9353    2.946966    3.724451    2.952228   
38389  ENSMUSG00000106640     Gm20940    2.946966    3.724451    2.952228   
38390  ENSMUSG00000106660     Gm43472    2.946966    3.724451    2.952228   
38391  ENSMUSG00000106955     Gm42960    2.946966    3.724451    2.952228   

       GSM5605688  GSM5605689  GSM5605690  GSM5605691  GSM5605692  
0        7.053638    6.870305    7.045505    7.018871    6.984234  
1        6.577912    6.729870    6.891201    6.783289    6.810631  
2        6.886796    6.693594    6.878948    6.768692    6.771620  
3        6.801952    6.619402    6.819337    6.796137    6.747208  
4        5.581302    6.691468    6.818334    6.690610    6.734524  
...           ...         ...         ...         ...         ...  
38387    2.773617    2.672702    2.797948    2.733644    2.738048  
38388    2.773617    2.672702    2.797948    2.733644    2.738048  
38389    2.773617    2.672702    2.797948    2.733644    2.738048  
38390    2.773617    2.672702    2.797948    2.733644    2.738048  
38391    2.773617    2.672702    2.797948    2.733644    2.738048  

[38392 rows x 10 columns]

In [10]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE185070-GPL21103-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE185070-GPL21103-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
